In [1]:
using Plots, LinearAlgebra, Random, StatsBase, SparseArrays, CSV, DataFrames

## Least-squares fitting with Stochastic Gradient Descent

We will rank sports teams using a variant of least squares 

In [8]:
## Read the data
using DataFrames
content = CSV.read("ncaa-2018.csv", DataFrame) 
# this file is also on the website in the same directory 

11824×13 DataFrame
   Row │ Date      Team                            Team Location  Team Score   ⋯
       │ String15  String                          String7        Int64        ⋯
───────┼────────────────────────────────────────────────────────────────────────
     1 │ 11/10/17  Eastern Kentucky                Away                   73   ⋯
     2 │ 11/10/17  Rice                            Home                   72
     3 │ 11/10/17  Southern Illinois-Edwardsville  Away                   74
     4 │ 11/10/17  Oral Roberts                    Home                   86
     5 │ 11/10/17  Purdue                          Home                  105   ⋯
     6 │ 11/10/17  Seattle                         Away                   46
     7 │ 11/10/17  Florida Atlantic                Away                   59
     8 │ 11/10/17  Saint Louis                     Home                   62
     9 │ 11/10/17  Hampton                         Away                   75   ⋯
    10 │ 11/10/17  Rider                           Home                   90
    11 │ 11/10/17  Greensboro                      Away                   80
   ⋮   │    ⋮                    ⋮                       ⋮            ⋮        ⋱
 11815 │ 3/11/18   Georgia State                   Neutral                74
 11816 │ 3/11/18   Tennessee                       Neutral                72   ⋯
 11817 │ 3/11/18   Texas-Arlington                 Neutral                61
 11818 │ 3/11/18   Houston                         Neutral                55
 11819 │ 3/11/18   Cincinnati                      Neutral                56
 11820 │ 3/11/18   Pennsylvania                    Neutral                68   ⋯
 11821 │ 3/11/18   Harvard                         Neutral                65
 11822 │ 3/11/18   Davidson                        Neutral                58
 11823 │ 3/11/18   Kentucky                        Neutral                77
 11824 │ 3/11/18   Rhode Island                    Neutral                57   ⋯
                                                9 columns and 11803 rows omitted

In [9]:
## Convert teams into numbers and also build our game table
m = size(content,1)
teams_dict = Dict{String,Int}()
teams = Vector{String}()
index = 1
data = Array{Int64}(undef, m, 4)
for i = 1 : m
    global index
    team = content[:Team][i]
    opponent = content[:Opponent][i]
    teamscore = content[Symbol("Team Score")][i]
    oppscore = content[Symbol("Opponent Score")][i]
    if !haskey(teams_dict, team)
        push!(teams, team)
        teams_dict[team] = index
        index = index + 1
    end

    if !haskey(teams_dict, opponent)
        push!(teams, opponent)
        teams_dict[opponent] = index
        index = index + 1
    end

    data[i, 1] = teams_dict[team]
    data[i, 2] = teams_dict[opponent]
    data[i, 3] = teamscore
    data[i, 4] = oppscore
end

LoadError: ArgumentError: syntax df[column] is not supported use df[!, column] instead

In [4]:
mutable struct SGD
    fs::Vector{Function} # we will randomly sample data
    x::Vector # current point
end
function gradient(M::SGD) # return the Gradient
    g = similar(M.x)
    fill!(g, zero(eltype(M.x)))
    for i=1:length(M.fs)
        g .+= gradient(M,i) # get the second output, which is the gradient
    end
    return g
end
function gradient(M::SGD, i::Int)
    return M.fs[i](M.x)[2]
end
## Setup least squares
function sports_loss(x,i,j,s)
    d = (x[i] - x[j] -s)
    f = 0.5*(d)^2
    g = zeros(length(x))
    g[i] = d
    g[j] = -d 
    return f, g
end
## 
opt = SGD(
    collect(map(game_i -> # game i maps to loss function i 
        (x -> sports_loss(x, data[game_i,1], data[game_i,2], 
                data[game_i,3] - data[game_i,4])),
        1:size(data,1))),
    zeros(length(teams_dict))
)
##
g = gradient(opt)
#m.fs[1](m.x)


LoadError: UndefVarError: data not defined

In [5]:
## Validate the gradient
m = size(data,1)
B = zeros(m, length(teams))
p = zeros(m)
for i=1:m
    # form the model
    ti = data[i,1]
    tj = data[i,2]
    p[i] = data[i,3] - data[i,4]
    B[i,ti] = 1
    B[i,tj] = -1
end
gtest = B'*(-p)
norm(g-gtest)

LoadError: UndefVarError: data not defined

In [6]:
function sgd_step!(m::SGD, alpha)
    f = rand(m.fs) # generate a random f
    m.x .-= alpha*f(m.x)[2]
end
norms = zeros(0)
for i=1:100 
    for j=1:100 # show gradient every few steps
        sgd_step!(opt, 0.001) # How to set alpha? 
    end
    push!(norms, norm(gradient(opt)))
end

LoadError: UndefVarError: opt not defined

In [7]:
plot(norms, label="", ylabel="norm(g)", yscale=:log10)

┌ Warning: No strict ticks found
└ @ PlotUtils ~/.julia/packages/PlotUtils/bZEEj/src/ticks.jl:191
┌ Warning: No strict ticks found
└ @ PlotUtils ~/.julia/packages/PlotUtils/bZEEj/src/ticks.jl:191
